# Car Ad Data Analysis
In this notebook, exploritory data analysis will be done on a data set containing information about used car listings. 

#### Project Sections:
1. Set Up: Loading in data and Packages, Cleaning Data
2. Exploritory Data Analysis:
    - Explore the relationship between the number of vehicles listed and make
    - Explore the relationship between model year, make, and price


### Section 1: Set Up 

In [1]:
# Import the necessary Packages 
import numpy as np
import pandas as pd
import plotly.express as px

# Read in and sample data 
df = pd.read_csv("..\\vehicles_us.csv")
df.sample(5)

price  model_year          model  condition  cylinders    fuel  \
6435    4995      2005.0   toyota prius       good        4.0     gas   
9526    5999      2001.0      ford f350  excellent       10.0     gas   
40880  28000      2016.0     gmc sierra   like new        8.0     gas   
25491   4750      2009.0   toyota prius  excellent        4.0  hybrid   
45088   6985      2013.0  ford focus se  excellent        4.0     gas   

       odometer transmission       type paint_color  is_4wd date_posted  \
6435   115700.0    automatic  hatchback       black     NaN  2019-04-06   
9526   123984.0    automatic     pickup        blue     NaN  2018-06-29   
40880   13400.0    automatic      truck         red     1.0  2018-06-14   
25491  159000.0    automatic  hatchback      silver     NaN  2018-05-14   
45088       NaN    automatic      sedan       black     NaN  2018-12-16   

       days_listed  
6435             7  
9526            47  
40880            7  
25491            3  
45088           77

In [2]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 51525 entries, 0 to 51524
Data columns (total 13 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   price         51525 non-null  int64  
 1   model_year    47906 non-null  float64
 2   model         51525 non-null  object 
 3   condition     51525 non-null  object 
 4   cylinders     46265 non-null  float64
 5   fuel          51525 non-null  object 
 6   odometer      43633 non-null  float64
 7   transmission  51525 non-null  object 
 8   type          51525 non-null  object 
 9   paint_color   42258 non-null  object 
 10  is_4wd        25572 non-null  float64
 11  date_posted   51525 non-null  object 
 12  days_listed   51525 non-null  int64  
dtypes: float64(4), int64(2), object(7)
memory usage: 5.1+ MB


#### Clean up the data

From the initial sampling of the data, the following data cleaning tasks should be proformed 
- Make Cylinders column an object data type and fill null values with 'unknown' because number of cylinders is catagorical data
- or the is_4wd column, fill Null values with 0 
- For the paint_color column, fill Null values with 'unknown'
- Drop rows with null values in the model year column (This will result in only dropping 9.7% of the data set)
- Replace null values in the odometer column with the yearly average
- Separate make and model into 2 columns 
- Make model_year and date_posted the datetime data type 

There are no duplicates in the data set. 

In [3]:
# Separate make and model into 2 columns 
df[['make', 'model']] = df['model'].str.split(' ',n=1, expand=True)

# Make model_year and date_posted the datetime data type 
df['model_year'] = pd.to_datetime(df['model_year'], format='%Y', errors='coerce').dt.year
df['date_posted'] = pd.to_datetime(df['date_posted'], format= '%Y-%m-%d')

# Verify Make and Model Column Corrections 
df.head(10)

price  model_year    model  condition  cylinders fuel  odometer  \
0   9400      2011.0       x5       good        6.0  gas  145000.0   
1  25500         NaN    f-150       good        6.0  gas   88705.0   
2   5500      2013.0   sonata   like new        4.0  gas  110000.0   
3   1500      2003.0    f-150       fair        8.0  gas       NaN   
4  14900      2017.0      200  excellent        4.0  gas   80903.0   
5  14990      2014.0      300  excellent        6.0  gas   57954.0   
6  12990      2015.0    camry  excellent        4.0  gas   79212.0   
7  15990      2013.0    pilot  excellent        6.0  gas  109473.0   
8  11500      2012.0  sorento  excellent        4.0  gas  104174.0   
9   9200      2008.0    pilot  excellent        NaN  gas  147191.0   

  transmission    type paint_color  is_4wd date_posted  days_listed      make  
0    automatic     SUV         NaN     1.0  2018-06-23           19       bmw  
1    automatic  pickup       white     1.0  2018-10-19           50      ford  
2    automatic   sedan         red     NaN  2019-02-07           79   hyundai  
3    automatic  pickup         NaN     NaN  2019-03-22            9      ford  
4    automatic   sedan       black     NaN  2019-04-02           28  chrysler  
5    automatic   sedan       black     1.0  2018-06-20           15  chrysler  
6    automatic   sedan       white     NaN  2018-12-27           73    toyota  
7    automatic     SUV       black     1.0  2019-01-07           68     honda  
8    automatic     SUV         NaN     1.0  2018-07-16           19       kia  
9    automatic     SUV        blue     1.0  2019-02-15           17     honda

In [4]:
# Make Cylinders column an object data type and fill null values with 'unknown'
df['cylinders'] = df['cylinders'].fillna('unknown')
# For the is_4wd column, fill Null values with 0 
df['is_4wd'] = df['is_4wd'].fillna(0)
# For the paint_color column, fill Null values with 'unknown'
df['paint_color'] = df['paint_color'].fillna('unknown')


In [5]:
# Replace null values in the odometer column with the yearly average
# Group by 'model_year' and calculate the average for 'odometer'
grouped_average = df.groupby('model_year')['odometer'].transform('mean')

# Use the grouped average to fill missing values in 'column_to_fill'
df['odometer'] = df['odometer'].fillna(grouped_average)

In [6]:
# Drop rows with null values in the model year column
df= df.dropna(axis='rows')

In [7]:
# Verify Datatype Corrections 
df.info()

<class 'pandas.core.frame.DataFrame'>
Index: 47905 entries, 0 to 51524
Data columns (total 14 columns):
 #   Column        Non-Null Count  Dtype         
---  ------        --------------  -----         
 0   price         47905 non-null  int64         
 1   model_year    47905 non-null  float64       
 2   model         47905 non-null  object        
 3   condition     47905 non-null  object        
 4   cylinders     47905 non-null  object        
 5   fuel          47905 non-null  object        
 6   odometer      47905 non-null  float64       
 7   transmission  47905 non-null  object        
 8   type          47905 non-null  object        
 9   paint_color   47905 non-null  object        
 10  is_4wd        47905 non-null  float64       
 11  date_posted   47905 non-null  datetime64[ns]
 12  days_listed   47905 non-null  int64         
 13  make          47905 non-null  object        
dtypes: datetime64[ns](1), float64(3), int64(2), object(8)
memory usage: 5.5+ MB


### 2. Exploritory Data Analysis

#### Number of Vehicles Listed By Make 

In [8]:
fig1 =px.histogram(df, x="make", title=' Number of Vehicles Listed by Make')
fig1.update_layout(xaxis_title='Vehicle Make ', yaxis_title='Number of Vehicles Listed')
fig1.show()

The majority of vehicles listed are made by Ford (12.6k) followed by Chevrolet (10.61k) and Toyota (5.4k). Mercedes has the least number of vehicles listed (41).

#### Make vs. Price

In [9]:
fig2 = px.scatter(df, x="model_year", y="price", color="make",
                title="Price vs. Model Year")
fig2.update_layout(xaxis_title='Model Year', yaxis_title='Price')
fig2.show()

There is a trend suggesting that the price of newer cars typicaly has a higher ceiling. I can also see an that Chevy's and Fords from the 1960's are an exception to that trend. 

In [10]:
fig = px.scatter(df, x="model_year", y="price", color="condition",
                title="Price vs. Model Year")
fig.update_layout(xaxis_title='Model Year', yaxis_title='Price')
fig.show()

We Can see that typically the lowest priced cars are salvage. Most cars listed are good, excellent, or like new. 

In [11]:
fig = px.scatter(df, x="odometer", y="price", color ="condition",
                title="Odometer Miles Vs Price")
fig.update_layout(xaxis_title='Odometer (Mi)', yaxis_title='Price')
fig.show()

As the miles on the car increases, the price decreases reguardless of condition. 

### Conclusion

The majority of vehicles listed are made by Ford (12.6k) followed by Chevrolet (10.61k) and Toyota (5.4k). Mercedes has the least number of vehicles listed (41). 

There is a trend suggesting that the price of newer cars typicaly has a higher ceiling. I can also see an that Chevy's and Fords from the 1960's are an exception to that trend. 

Typically the lowest priced cars are salvage. Most cars listed are good, excellent, or like new. As the miles on the car increases, the price decreases reguardless of condition. 